In [1]:
import pandas as pd
import dgl

2022-09-21 12:42:11.498523: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-09-21 12:42:11.514215: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-09-21 12:42:11.514563: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-09-21 12:42:11.517294: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags

In [2]:
dataset = pd.read_csv('data/RecipeNLG_dataset.csv',index_col=[0])

In [3]:
dataset.columns

Index(['title', 'ingredients', 'directions', 'link', 'source', 'NER'], dtype='object')

In [4]:
dataset.head()

title                                        ingredients  \
0    No-Bake Nut Cookies  ["1 c. firmly packed brown sugar", "1/2 c. eva...   
1  Jewell Ball'S Chicken  ["1 small jar chipped beef, cut up", "4 boned ...   
2            Creamy Corn  ["2 (16 oz.) pkg. frozen corn", "1 (8 oz.) pkg...   
3          Chicken Funny  ["1 large whole chicken", "2 (10 1/2 oz.) cans...   
4   Reeses Cups(Candy)    ["1 c. peanut butter", "3/4 c. graham cracker ...   

                                          directions  \
0  ["In a heavy 2-quart saucepan, mix brown sugar...   
1  ["Place chipped beef on bottom of baking dish....   
2  ["In a slow cooker, combine all ingredients. C...   
3  ["Boil and debone chicken.", "Put bite size pi...   
4  ["Combine first four ingredients and press in ...   

                                              link    source  \
0   www.cookbooks.com/Recipe-Details.aspx?id=44874  Gathered   
1  www.cookbooks.com/Recipe-Details.aspx?id=699419  Gathered   
2   www.cookbooks.com/Recipe-Details.aspx?id=10570  Gathered   
3  www.cookbooks.com/Recipe-Details.aspx?id=897570  Gathered   
4  www.cookbooks.com/Recipe-Details.aspx?id=659239  Gathered   

                                                 NER  
0  ["brown sugar", "milk", "vanilla", "nuts", "bu...  
1  ["beef", "chicken breasts", "cream of mushroom...  
2  ["frozen corn", "cream cheese", "butter", "gar...  
3  ["chicken", "chicken gravy", "cream of mushroo...  
4  ["peanut butter", "graham cracker crumbs", "bu...

In [5]:
dataset = dataset.drop(['link','source'],axis=1)

In [6]:
print(len(list(dataset['title'])))
print(len(list(dataset['title'].unique())))


2231142
1312871


In [7]:
dataset['title'] += '_' + dataset.groupby('title').cumcount().add(1).map(str)

In [8]:
titles = list(dataset['title'].unique())
titles = [x.lower() for x in titles]
titles_to_id = dict(zip(titles,range(len(titles))))

In [9]:
ner = list(dataset["NER"])
ingredients = set()
for x in ner:
    cleaned_ingredients = x.replace('[','')
    cleaned_ingredients = cleaned_ingredients.replace(']','')
    for y in cleaned_ingredients.split(","):
        y = y.replace("\"","")
        y = y.lower()
        ingredients.add(y.strip())
        

In [10]:
ingredients_to_id = dict(zip(ingredients,range(len(ingredients))))

In [11]:
from ast import literal_eval

df = dataset[["title","NER"]]
df["NER"] = df["NER"].apply(literal_eval)


/home/edo/.conda/envs/tesi/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [12]:
df = df.explode("NER")

In [13]:
df = df[df['NER'].isnull() == False]

In [14]:
df.values

array([['No-Bake Nut Cookies_1', 'brown sugar'],
       ['No-Bake Nut Cookies_1', 'milk'],
       ['No-Bake Nut Cookies_1', 'vanilla'],
       ...,
       ['Polpette in Spicy Tomato Sauce_1', 'Salt'],
       ['Polpette in Spicy Tomato Sauce_1', 'tomato sauce'],
       ['Polpette in Spicy Tomato Sauce_1', 'red pepper']], dtype=object)

In [15]:
from scipy.sparse import coo_matrix
import numpy as np
row = []
columns = []
for x in df.values:
    try:
        cleaned_ingredient = x[1].replace("\"","")\
                                 .replace(",","")\
                                 .replace("[","")\
                                 .replace("]","")\
                                 .lower().strip()
        columns.append(ingredients_to_id[cleaned_ingredient])
        row.append(titles_to_id[x[0].lower()])
    except Exception as e:
        print("Exception" , e)
        print(cleaned_ingredient)
        print(x)

Exception 'light\tmiracle'
light	miracle
['Seven Layer Salad_58' 'light\tMiracle']
Exception 'sautéed onion'
sautéed onion
['Squash Casserole_676' 'sautéed onion']
Exception 'sautéed onion'
sautéed onion
['Broccoli Salad_456' 'sautéed onion']
Exception 'fresh) boiling'
fresh) boiling
['Family Spinach_1' 'fresh), boiling']
Exception 'ground road'
ground road
["Gary'S Chili_2" 'ground "road']
Exception 'kirsch liqueur'
kirsch liqueur
['Fresh Cherry Pie_4' '"Kirsch Liqueur']
Exception 'carmel chicken'
carmel chicken
['Soy "Chicken" And Dumplings_1' 'carmel "chicken']
Exception 'sautéed mushrooms'
sautéed mushrooms
["Mom'S Meat Loaf_35" 'sautéed mushrooms']
Exception 'full of sugar'
full of sugar
['Recipe For Take Out_1' 'full of "sugar']
Exception 'frozen hash brown bricks'
frozen hash brown bricks
["Grandma Jacobs' Hash Brown Casserole_1" 'frozen hash brown "bricks']
Exception 'nilla® waters'
nilla® waters
['Hot Chocolate Truffles_1' 'NILLA® waters']
Exception 'swiss miss®'
swiss miss®
[

['No Yolks® Lamb Stew_1' 'NO YOLKS®']
Exception 'hormel® chili no beans'
hormel® chili no beans
['Chili Dogs With Cheese_1' 'HORMEL® Chili No Beans']
Exception 'clamato®'
clamato®
['Clamato® Cooked Salmon_1' 'Clamato®']
Exception 'velveeta®'
velveeta®
['Velveeta® Italian Sausage Bake_1' 'VELVEETA®']
Exception "campbell's®"
campbell's®
['Creamy Poblano Mac & Cheese_1' "Campbell's®"]
Exception "'s® cocoa"
's® cocoa
["S'Mores Pieces Cheesecake_1" "'S® Cocoa"]
Exception "campbell's®"
campbell's®
['15-Minute Herbed Chicken_1' "Campbell's®"]
Exception 'buitoni®'
buitoni®
['Garlic Shrimp With Three Cheese Tortellini_1' 'BUITONI®']
Exception 'buitoni®'
buitoni®
['Garlic Shrimp With Three Cheese Tortellini_1' 'BUITONI®']
Exception "campbell's®"
campbell's®
['Cornbread Chicken Pot Pie_1' "Campbell's®"]
Exception "campbell's®"
campbell's®
['2-Step Skillet Chicken Broccoli Divan_1' "Campbell's®"]
Exception 'clamato®'
clamato®
['Clamato® Bloody Caesar_1' 'Clamato®']
Exception 'barilla® elbows'
bari

Exception 'hormel®'
hormel®
['Mini Corned Beef Quiche_1' 'HORMEL®']
Exception 'barilla®'
barilla®
["Mom'S Homestyle Barilla® Gluten Free Macaroni Salad_1" 'Barilla®']
Exception 'sparkling rosé wine'
sparkling rosé wine
['Festive Fizz_1' 'sparkling rosé wine']
Exception "campbell's®"
campbell's®
['Mini Cheesy Chicken Enchiladas_1' "Campbell's®"]
Exception '’s'
’s
["Boar'S Head Bold® Ichiban Teriyaki™ Style Chicken Salad_1" '’s']
Exception "campbell's®"
campbell's®
['Mini Chicken And Stuffing Cups_1' "Campbell's®"]
Exception 'buitoni®'
buitoni®
['Firecracker Pasta Salad_1' 'BUITONI®']
Exception 'buitoni®'
buitoni®
['Firecracker Pasta Salad_1' 'BUITONI®']
Exception "campbell's®"
campbell's®
['Salsa Mac And Beef_1' "Campbell's®"]
Exception 'barilla®'
barilla®
['Barilla® Gluten Free Rotini With Charred Green Onion Pesto, Cashews, And Cranberries_1'
 'Barilla®']
Exception 'bitters®'
bitters®
['Sazerac Cocktail_1' 'Bitters®']
Exception "'s®"
's®
['Kisses Peppermint Brownie Drops_1' "'S®"]
Exc

Exception 'kitchen®'
kitchen®
['Strawberry Coconut Milk Smoothie_1' 'Kitchen®']
Exception "'s®"
's®
['Individual Swirled Pumpkin Cheesecakes_1' "'S®"]
Exception 'cocoa krispies®'
cocoa krispies®
['Chick & Egg Krispies Nest Easter Treats_1' 'COCOA KRISPIES®']
Exception 'cocoa krispies®'
cocoa krispies®
['Milky Way Balls_1' 'COCOA KRISPIES®']
Exception 'gold medal®'
gold medal®
['Vegan Sugar Cookies_2' 'Gold Medal®']
Exception "'s®"
's®
["Libby'S® Pumpkin Roll_1" "'S®"]
Exception 'cocoa krispies®'
cocoa krispies®
['Cocoa Granola Bars_1' 'COCOA KRISPIES®']
Exception 'fisher® pecan halves'
fisher® pecan halves
['Pecan-Crusted Green Bean Casserole_1' 'Fisher® Pecan Halves']
Exception 'fisher® pecan halves'
fisher® pecan halves
['Pecan-Crusted Green Bean Casserole_1' 'Fisher® Pecan Halves']
Exception "'s®"
's®
['Black Bean Fiesta With Yellow Rice & Shrimp #Rsc_1' "'S®"]
Exception '’s italian'
’s italian
['Chunky Pizza Sauce_1' '’s Italian']
Exception 'archer farms®'
archer farms®
['Tandoori 

Exception 'crème de cacao'
crème de cacao
['Cappucino Cooler_1' 'Crème de Cacao']
Exception 'crème'
crème
['Mini Blackcurrant Cheesecakes_1' 'crème']
Exception 'tomato purée'
tomato purée
['Turkey Salami Pizza With Salad_1' 'tomato purée']
Exception 'tomato purée'
tomato purée
['Mushroom And Olive Flatbread Pizza_1' 'tomato purée']
Exception 'crème fraîche'
crème fraîche
['Mussels With Chorizo_1' 'crème fraîche']
Exception 'crème fraîche'
crème fraîche
['Creamy Bacon And Mushroom Pasta With Romaine Lettuce_1' 'crème fraîche']
Exception 'crème fraîche'
crème fraîche
['Stuffed Potatoes_60' 'crème fraîche']
Exception 'cachaça'
cachaça
['Strawberry Caipirinha_2' 'cachaça']
Exception 'mixed glacé fruit'
mixed glacé fruit
['Frozen Chocolate Christmas Pudding_1' 'mixed glacé fruit']
Exception 'glacé cherries'
glacé cherries
['Frozen Chocolate Christmas Pudding_1' 'glacé cherries']
Exception 'tomato purée'
tomato purée
['Spaghetti And Meatballs In Tomato Cream Sauce_1' 'tomato purée']
Exceptio

...

Exception '¼'
¼
['Lemon Meringue Cheesecake Trifle_1' '¼']
Exception 'jif®'
jif®
['Pb&J Banana Dogs_1' 'Jif®']
Exception '¼'
¼
["Bailey'S Chocolate Mousse_2" '¼']
Exception 'shady brook farms® turkey'
shady brook farms® turkey
['Oven-Fried Turkey Drumsticks_1' 'Shady Brook Farms® Turkey']
Exception '¼'
¼
['Slow Cooker Turkey Meatloaf_1' '¼']
Exception 'sabra®'
sabra®
['Creamy Bruschetta Dip_1' 'Sabra®']
Exception '™'
™
['Lemon-Cream Cheese Crescent Ring_1' '™']
Exception 'pork rub mccormick®'
pork rub mccormick®
['Kansas City Pulled Pork_2' 'pork rub McCormick®']
Exception 'pretzels – crushed'
pretzels – crushed
['Chocolate Pretzel Cookies!!!_1' 'pretzels – crushed']
Exception 'knorr® chicken flavor'
knorr® chicken flavor
['Potato Poblano Enchiladas_1' 'Knorr® Chicken flavor']
Exception 'gruyère'
gruyère
['Roasted Cauliflower And GruyèRe Frittata_1' 'gruyère']
Exception 'cilantro knorr®'
cilantro knorr®
['Creamy Nopales Dip_1' 'cilantro Knorr®']
Exception 'tomato purée'
tomato purée
[

Exception '¼'
¼
['Creamy Cheesy Ham Tomato Sauce_1' '¼']
Exception 'chèvre'
chèvre
['Goat Cheese Salad_3' 'Chèvre']
Exception 'gruyére'
gruyére
['Swiss Inspired Onion Quiche_1' 'Gruyére']
Exception 'mozzarella – shredded'
mozzarella – shredded
['Egg & Bean Omelet_1' 'mozzarella – shredded']
Exception 'tomato purée'
tomato purée
['Spaghetti Bake With Bacon And Tomatoes_2' 'tomato purée']
Exception '½oz'
½oz
["Pesto, Goats' Cheese And Vegetable Bagel_1" '½oz']
Exception 'wish bone ®'
wish bone ®
['Italian-Style Pasta Salad_3' 'wish bone ®']
Exception '’s milk'
’s milk
['Jt’S Famous Mediterranean Pasta_1' '’s milk']
Exception 'crème fraîche'
crème fraîche
['Scallops Florentine_7' 'crème fraîche']
Exception 'whipping cream 动物鲜奶油'
whipping cream 动物鲜奶油
['Chocolate Cranberry Cupcakes_1' 'whipping cream 动物鲜奶油']
Exception '’s original'
’s original
['Breaded Pork Tenderloin Sandwich_2' '’s Original']
Exception 'tomato purée'
tomato purée
['Schnitzel With French Fries And Bell Pepper Sauce_2' 'to

Exception 'pastry flour>flour'
pastry flour>flour
["Apple Pie Crumble (Wolfgang Puck's) Desserts Recipe_1"
 'pastry flour">flour']
Exception 'medium wide noodles>noodles'
medium wide noodles>noodles
['Beef Noodle Soup Recipe_1' 'medium wide noodles">noodles']
Exception 'black raisins>raisins'
black raisins>raisins
['A Glorious Plum Pudding For Christmas Pt 1 Recipe_1'
 'black raisins">raisins']
Exception 'soy steak'
soy steak
['Hunan-Style Orange ?Beef? and Asparagus Stir-Fry_1' 'soy "steak']
Exception 'leeks>spring onions'
leeks>spring onions
['Barbecued Seafood Skewers With Sun Dried Tomato Basil Aio Recipe_1'
 'leeks">Spring onions']
Exception 'chips>chocolate chips'
chips>chocolate chips
['Two Tone Cream Pie Recipe_1' 'chips">chocolate chips']
Exception 'white red'
white red
['"Haute" TexMex Chili Recipe gabor fischer_1' 'White, red']
Exception 'butter>butter'
butter>butter
['Maryland Crab Cakes Recipe_1' 'butter">butter']
Exception 'red pepper>pepper'
red pepper>pepper
['"Chinese"

Exception 'white wine>wine'
white wine>wine
['Braised Sausages With Polenta Recipe_1' 'White wine">Wine']
Exception 'banana(mashed)(adds sweet'
banana(mashed)(adds sweet
['Big Cookie Ww Recipe_1' 'Banana,(mashed)(adds sweet']
Exception 'salt>salt'
salt>salt
['Green Pepper Stuffing Recipe_1' 'salt">Salt']
Exception 'brown sugar>sugar'
brown sugar>sugar
['Any Fruit Will Do Muffins With Streusal Topping Pt1 Recipe_1'
 'Brown sugar">sugar']
Exception 'extra virgin olive-oil>olive oil'
extra virgin olive-oil>olive oil
['Cajun Popcorn Recipe_1' 'Extra virgin olive-oil">olive oil']
Exception 'salt>salt'
salt>salt
['Curry Chicken (Jamaican) Recipe_1' 'salt">salt']
Exception 'onion powder\\flakes'
onion powder\flakes
['Omelette Sandwich (Egg Bake)_1' 'onion powder\\flakes']
Exception 'sugar>sugar'
sugar>sugar
['Braised Duck (Or Mussels) With Red Curry Recipe_1' 'sugar">sugar']
Exception 'chips>chocolate chips'
chips>chocolate chips
['Apple Chip Snacking Cake Recipe_1' 'chips">Chocolate Chips']


Exception 'broth>broth'
broth>broth
['Creamed Turkey With Biscuits Recipe_1' 'broth">broth']
Exception 'vegetable oil.enough'
vegetable oil.enough
['Deep Fried Cajun Catfish Fingers_1' 'vegetable oil,.enough']
Exception 'tomatoes>tomatoes'
tomatoes>tomatoes
['Louisiana Creole Roast Recipe_1' 'tomatoes">tomatoes']
Exception 'tomatoes>tomatoes'
tomatoes>tomatoes
['Beef Oven Stew With Meatballs Recipe_1' 'tomatoes">Tomatoes']
Exception 'maple-sugar>maple'
maple-sugar>maple
['Smoked Pork Chops With Apples Recipe_2' 'maple-sugar">maple']
Exception 'whole wheat flour>flour'
whole wheat flour>flour
['100% Whole Wheat Loaf Recipe_1' 'whole wheat flour">flour']
Exception 'bran>bran'
bran>bran
['Luscious Diet Apricot Bars Recipe_1' 'bran">bran']
Exception 'brown lentils>lentils'
brown lentils>lentils
['Barley Pilaf With Lentil Confetti Recipe_1' 'brown lentils">lentils']
Exception 'whole wheat flour>flour'
whole wheat flour>flour
['Tomato Pie Recipe_5' 'whole wheat flour">flour']
Exception 'toma

In [55]:
import numpy as np
ids = np.arange(0,len(titles))
edge_ids = []
for x in df.values:
    try:

array([['No-Bake Nut Cookies_1', 'brown sugar'],
       ['No-Bake Nut Cookies_1', 'milk'],
       ['No-Bake Nut Cookies_1', 'vanilla'],
       ...,
       ['Polpette in Spicy Tomato Sauce_1', 'Salt'],
       ['Polpette in Spicy Tomato Sauce_1', 'tomato sauce'],
       ['Polpette in Spicy Tomato Sauce_1', 'red pepper']], dtype=object)

In [16]:
adj_matrix = coo_matrix((np.ones(len(row)),(row,columns)), shape=(len(titles),len(ingredients)))

In [47]:
adj_matrix

<2231142x198600 sparse matrix of type '<class 'numpy.float64'>'
	with 18871128 stored elements in COOrdinate format>

In [21]:
g = dgl.bipartite_from_scipy(adj_matrix,"recipe","contain","ingredient")

In [25]:
dgl.sampling.sample_neighbors(g.recipe, [0, 1], 5)

AttributeError: 'DGLHeteroGraph' object has no attribute 'recipe'

In [26]:
dgl.save_graphs("graph",g)

In [33]:
dgl.sampling.PinSAGESampler(g, "recipe", "ingredient", 3, 0.5, 200, 10)

KeyError: 'recipe'

{}